In [1]:
import pickle
import pandas as pd
from datetime import timedelta, datetime
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import os
if os.path.basename(os.getcwd())=="Simulations":
    os.chdir('..')
    os.chdir('..')
    os.chdir('..') ## to work at project root  like in any IDE

InputFolder='Models/Belfort/Simulations/'
from Models.Belfort.Simulations.f_consumptionBelfort import *

# 1. Import data

In [2]:
Temp_df=pd.read_csv('Models/Belfort/Conso/Temp_FR_2017_2022.csv',sep=';',decimal='.',parse_dates=['Date']).set_index(["Date"])

index2019=(Temp_df.index.to_series().dt.minute==0)&(Temp_df.index.to_series().dt.year==2019)
Temp_2019_df=Temp_df[index2019].reset_index().set_index("Date").sort_index()
Temp_2019_df= CleanCETIndex(Temp_2019_df)# Traitement heure d'été et heure d'hiver

In [3]:
Conso_2019_df=pd.read_csv('Models/Belfort/Conso/areaConsumption2019_FR.csv',sep=';',parse_dates=['Date']).set_index(["Date"])

In [14]:
year=2050
nuc="nuclear_plus_plus"
type_result="multinode_"#"" if singlenode
no_stock_fr=False
d_stock_fr={True:"_no_stock_fr",False:""}
no_new_intercos=False
d_no_new_intercos={True:"_no_new_intercos",False:""}
bati_hyp="ref"
reindus="reindus"
with open(InputFolder+"Results_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus+d_stock_fr[no_stock_fr]+d_no_new_intercos[no_new_intercos]+".pickle", 'rb') as f:
    Variables=pickle.load(f)

In [3]:
print(Variables)

{'power_Dvar':        AREAS                TIME   TECHNOLOGIES   power_Dvar
0         BE 2019-04-24 20:00:00        OldNuke     0.000000
1         BE 2019-04-24 20:00:00          Solar     0.000000
2         BE 2019-04-24 20:00:00        Biomass     0.000000
3         BE 2019-04-24 20:00:00    WindOnShore  4882.538437
4         BE 2019-04-24 20:00:00            CCG     0.000000
...      ...                 ...            ...          ...
858475    IT 2019-02-09 23:00:00  NewHydroRiver     0.000000
858476    IT 2019-02-09 23:00:00        NewNuke     0.000000
858477    IT 2019-02-09 23:00:00    curtailment     0.000000
858478    IT 2019-02-09 23:00:00     HydroRiver  6897.729469
858479    IT 2019-02-09 23:00:00   WindOffShore    84.500000

[858480 rows x 4 columns], 'exchange_Pvar':        AREAS AREAS                TIME  exchange_Pvar
0         BE    BE 2019-04-24 20:00:00            0.0
1         BE    BE 2019-05-07 09:00:00            0.0
2         BE    BE 2019-10-15 01:00:00        

In [4]:
StockTechnos_df=pd.read_csv("Models/Belfort/Prod/Prod_Europe/Stock_technos_Europe_"+str(year)+".csv",
                            delimiter=";",decimal=",").set_index(['AREAS','STOCK_TECHNO'])

# 2. Tools

## 2.1. Capacity

In [6]:
def prod_capa(area):
    df=Variables['capacity_Dvar']
    if area!='EU':
        return df[df.AREAS==area].set_index(['AREAS','TECHNOLOGIES']).sort_index()[['capacity_Dvar']]
    else:
        return df.groupby(['TECHNOLOGIES']).sum().sort_index()[['capacity_Dvar']]

def stock_capa(area):
    df1=Variables['Pmax_in_Dvar'].set_index(['AREAS','STOCK_TECHNO'])
    df2=Variables['Pmax_out_Dvar'].set_index(['AREAS','STOCK_TECHNO'])
    df3=Variables['Cmax_Pvar'].set_index(['AREAS','STOCK_TECHNO'])
    df1['Pmax_out_Dvar']=df2['Pmax_out_Dvar']
    df1['Cmax_Pvar']=df3['Cmax_Pvar']
    df1['hour_stock']=df1['Cmax_Pvar']/(df1['Pmax_in_Dvar']*StockTechnos_df['efficiency_in'])
    df1=df1.fillna(0)
    return df1.loc[(area,slice(None)),['Pmax_in_Dvar','Pmax_out_Dvar','Cmax_Pvar','hour_stock']].sort_index()

def flex_capa(area):
    df=Variables['increased_max_power_Dvar']
    return df[df.AREAS==area].set_index(['AREAS','FLEX_CONSUM']).sort_index()[['increased_max_power_Dvar']]


In [7]:
# Production means capacity (MW)
prod_capa('FR')

capacity_Dvar
AREAS TECHNOLOGIES                 
FR    Biomass           3000.000000
      CCG                  0.000000
      Coal                 0.000000
      Geothermal           0.000000
      HydroReservoir    8785.000000
      HydroRiver       11030.000000
      NewHydroRiver     1200.000000
      NewNuke          26730.000000
      OldNuke          13870.000000
      Solar           160215.865202
      TAC                  0.000000
      WindOffShore     49000.000000
      WindOnShore      37000.000000
      curtailment          0.000000

In [9]:
prod_capa('EU')

capacity_Dvar
TECHNOLOGIES                 
Biomass          21267.000000
CCG                  0.000000
Coal                 0.000000
Geothermal         800.000000
HydroReservoir   41770.000000
HydroRiver       34680.000000
NewHydroRiver     1200.000000
NewNuke          54160.000000
OldNuke          15058.000000
Solar           854215.670409
TAC                  0.000000
WindOffShore    320888.630255
WindOnShore     426180.694726
curtailment          0.000000

In [10]:
stock_capa('FR')

Pmax_in_Dvar  Pmax_out_Dvar     Cmax_Pvar  hour_stock
AREAS STOCK_TECHNO                                                           
FR    Battery            6445.566657    6445.566657  6.784807e+03    1.108033
      HydroStorage      10899.000000   10899.000000  1.961820e+05   20.000000
      PowertoH2toPower  17755.324507       0.000000  1.742103e+06  140.167470

In [11]:
flex_capa('FR')

increased_max_power_Dvar
AREAS FLEX_CONSUM                          
FR    EV                       21076.487902
      Steel                        0.000000

## 2.2. Energy

In [12]:
def energy(area):
    df=Variables['power_Dvar']
    if area!='EU':
        df=df[df.AREAS==area]
        df=df.groupby(['AREAS','TECHNOLOGIES']).sum()
    else:
        df=df.groupby(['TECHNOLOGIES']).sum()
    df_capa=prod_capa(area)
    df['Load_factor']=df['power_Dvar']/(8760*df_capa['capacity_Dvar'])
    E=df['power_Dvar'].sum()
    df['Part']=df['power_Dvar']/E
    df=df.fillna(0)
    return df

In [13]:
energy('FR')

power_Dvar  Load_factor      Part
AREAS TECHNOLOGIES                                       
FR    Biomass         1.500000e+07     0.570776  0.018586
      CCG             0.000000e+00     0.000000  0.000000
      Coal            0.000000e+00     0.000000  0.000000
      Geothermal      0.000000e+00     0.000000  0.000000
      HydroReservoir  1.437226e+07     0.186758  0.017808
      HydroRiver      4.918008e+07     0.508990  0.060936
      NewHydroRiver   4.996534e+06     0.475317  0.006191
      NewNuke         1.906650e+08     0.814269  0.236241
      OldNuke         8.681043e+07     0.714482  0.107561
      Solar           2.203239e+08     0.156983  0.272989
      TAC             0.000000e+00     0.000000  0.000000
      WindOffShore    1.440876e+08     0.335681  0.178530
      WindOnShore     8.164343e+07     0.251893  0.101159
      curtailment     0.000000e+00     0.000000  0.000000

In [14]:
energy('EU')

power_Dvar  Load_factor      Part
TECHNOLOGIES                                       
Biomass         1.063350e+08     0.570776  0.030034
CCG             0.000000e+00     0.000000  0.000000
Coal            0.000000e+00     0.000000  0.000000
Geothermal      6.934695e+06     0.989540  0.001959
HydroReservoir  5.221887e+07     0.142711  0.014749
HydroRiver      1.538044e+08     0.506274  0.043442
NewHydroRiver   4.996534e+06     0.475317  0.001411
NewNuke         3.761712e+08     0.792871  0.106248
OldNuke         9.398241e+07     0.712484  0.026545
Solar           1.036354e+09     0.138496  0.292714
TAC             0.000000e+00     0.000000  0.000000
WindOffShore    9.231471e+08     0.328407  0.260740
WindOnShore     7.865502e+08     0.210683  0.222158
curtailment     0.000000e+00     0.000000  0.000000

In [7]:
def energy_years(area,nuclear_plus_minus=True):
    df_ret=pd.DataFrame()
    for year in [2030,2040,2050,2060]:
        if year==2030 and nuc!='nuclear_plus_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        elif year!=2060 or not nuclear_plus_minus or nuc!='nuclear_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        else:
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_minus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        
        df=Variables_year['power_Dvar']
        df=df[df.AREAS==area]
        df=df.groupby('TECHNOLOGIES').sum()
        df_ret[str(year)]=df['power_Dvar']
    
    return df_ret

def save_energy_years(df,area):
    df.to_csv(InputFolder+"Costs/Production_"+area+"_"+nuc+"_"+reindus+"_"+bati_hyp+".csv",sep=";",decimal=",",encoding="utf-8")
        

In [15]:
df=energy_years('FR')
save_energy_years(df,'FR')

## 2.3. Plots

In [18]:
def filter_variable(name,area,month_ini,day_ini,month_end,day_end):
    df=Variables[name]
    if month_ini==month_end:
        df=df[(df.AREAS==area)&(df.TIME.dt.month>=month_ini)&(df.TIME.dt.day>=day_ini)\
         &(df.TIME.dt.month<=month_end)&(df.TIME.dt.day<=day_end)]
    else:
        df=df[(df.AREAS==area)&(((df.TIME.dt.month==month_ini)&(df.TIME.dt.day>=day_ini))\
             |((df.TIME.dt.month<month_end)&(df.TIME.dt.month>month_ini))\
             |((df.TIME.dt.month==month_end)&(df.TIME.dt.day<=day_end)))]
    return df

def plot_prod(area,month_ini,day_ini,month_end,day_end,title=""):
    df_prod=filter_variable('power_Dvar',area,month_ini,day_ini,month_end,day_end)
    df_sto_in=filter_variable('storageIn_Pvar',area,month_ini,day_ini,month_end,day_end)
    df_sto_out=filter_variable('storageOut_Pvar',area,month_ini,day_ini,month_end,day_end)
        
    df_exchange=Variables['exchange_Pvar']
    df_exchange.columns=['AREAS_from','AREAS','TIME','exchange_Pvar']
    df_exchange=df_exchange[(df_exchange.AREAS==area)&(df_exchange.TIME.dt.month>=month_ini)\
                                &(df_exchange.TIME.dt.day>=day_ini)\
         &(df_exchange.TIME.dt.month<=month_end)&(df_exchange.TIME.dt.day<=day_end)]
        
        
    df_prod=df_prod.pivot(index=['AREAS','TIME'], columns='TECHNOLOGIES', values='power_Dvar')
    df_sto_in=df_sto_in.pivot(index=['AREAS','TIME'], columns='STOCK_TECHNO', values='storageIn_Pvar')
    df_sto_out=df_sto_out.pivot(index=['AREAS','TIME'], columns='STOCK_TECHNO', values='storageOut_Pvar')
        
    df_exchange=df_exchange.pivot(index=['AREAS','TIME'], columns='AREAS_from', values='exchange_Pvar')
        
    df=pd.DataFrame()
    df['Nucléaire']=df_prod['OldNuke']+df_prod['NewNuke']
    df['Bioénergies et autres ENR']=df_prod['Biomass']+df_prod['Geothermal']
    df['Éolien']=df_prod['WindOffShore']+df_prod['WindOnShore']
    df['Solaire']=df_prod['Solar']
    df['Hydraulique']=df_prod['HydroRiver']+df_prod['NewHydroRiver']+df_prod['HydroReservoir']
    df['Gaz']=df_prod['CCG']+df_prod['TAC']
    df['Charbon']=df_prod['Coal']
        
    df['Injections batteries']=df_sto_out['Battery']
    df['Turbinage STEP']=df_sto_out['HydroStorage']
    df['Hydrogen-to-power']=df_sto_out['PowertoH2toPower']
        
    df['Imports']=sum(df_exchange[col] for col in df_exchange.columns)
        
    df['Soutirage batteries']=-df_sto_in['Battery']
    df['Pompage STEP']=-df_sto_in['HydroStorage']
    df['Power-to-hydrogen']=-df_sto_in['PowertoH2toPower']
        
    df['Exports']=df['Imports'].apply(lambda x: x if x<0 else 0)
    df['Imports']=df['Imports'].apply(lambda x: x if x>=0 else 0)
        
    d_colors={'Nucléaire':'yellow','Bioénergies et autres ENR':'darkgreen',
                 'Éolien':'lightskyblue','Solaire':'orange','Hydraulique':'blue',
                 'Gaz':'red','Charbon':'saddlebrown','Injections batteries':'magenta',
                 'Turbinage STEP':'navy','Hydrogen-to-power':'purple','Imports':'gray',
                 'Soutirage batteries':'magenta','Pompage STEP':'navy',
                 'Power-to-hydrogen':'purple','Exports':'gray'}
    
    df.reset_index(inplace=True)
    df['TIME']=df['TIME'].apply(lambda x: x.replace(year=year))
        
    fig=go.Figure()
    for col in df.columns:
        if col not in ['AREAS','TIME','Soutirage batteries','Pompage STEP','Power-to-hydrogen','Exports']:
            fig.add_trace(go.Scatter(x= df['TIME'], y = df[col]/1000,
                                     name = col,
                                     line=dict(width=0, color=d_colors[col]),
                                     stackgroup = '+'))
        elif col in ['Soutirage batteries','Pompage STEP','Power-to-hydrogen','Exports']:
            fig.add_trace(go.Scatter(x= df['TIME'], y = df[col]/1000,
                                     name = col,
                                     line=dict(width=0, color=d_colors[col]),
                                     stackgroup = '-'))
                
    fig.update_layout(title =title,
                           title_font_size = 20,width = 1000, height = 500)
    fig.update_yaxes(title_text = 'Puissance (GW)')
    return fig

def plot_prod_and_save(area,month_ini,day_ini,month_end,day_end,title=""):
    fig=plot_prod(area,month_ini,day_ini,month_end,day_end,title)
    fig.write_image(InputFolder+"Graphs/Prod_"+area+"_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus\
                         +"_"+str(day_ini)+"_"+str(month_ini)+"_"+str(day_end)+"_"+str(month_end)+".png")
        
        

In [26]:
# Ça n'a rien à faire ici, mais c'est très joli !
plot_prod('FR',7,22,7,28)
#plot_prod_and_save('FR',7,22,7,28)

In [27]:
def h2_curve(area,month_ini,day_ini,month_end,day_end):
    df_sto_in=filter_variable('storageIn_Pvar',area,month_ini,day_ini,month_end,day_end)
    df_sto_in=df_sto_in[df_sto_in.STOCK_TECHNO=='PowertoH2toPower']
    df=pd.DataFrame()
    df['Power-to-hydrogen']=df_sto_in['storageIn_Pvar']
    df['TIME']=df_sto_in['TIME']
    df['TIME']=df['TIME'].apply(lambda x: x.replace(year=year))
    df=df.set_index('TIME').sort_index()
    return df

In [28]:
h2_curve('FR',6,16,6,16)

Power-to-hydrogen
TIME                                  
2050-06-16 00:00:00       17755.324507
2050-06-16 01:00:00       17755.324507
2050-06-16 02:00:00       17755.324507
2050-06-16 03:00:00       17755.324507
2050-06-16 04:00:00       17755.324507
2050-06-16 05:00:00       17755.324507
2050-06-16 06:00:00       17755.324507
2050-06-16 07:00:00       17755.324507
2050-06-16 08:00:00       17755.324507
2050-06-16 09:00:00       17755.324507
2050-06-16 10:00:00       17755.324507
2050-06-16 11:00:00       17755.324507
2050-06-16 12:00:00       17755.324507
2050-06-16 13:00:00       17755.324507
2050-06-16 14:00:00       17755.324507
2050-06-16 15:00:00       17755.324507
2050-06-16 16:00:00       17755.324507
2050-06-16 17:00:00       17755.324507
2050-06-16 18:00:00       17755.324507
2050-06-16 19:00:00       17755.324507
2050-06-16 20:00:00        7181.043033
2050-06-16 21:00:00           0.000000
2050-06-16 22:00:00           0.000000
2050-06-16 23:00:00           0.000000

## 2.4. Thermosensitivity

In [29]:
def moyenne_dict(d):
    return 1/max(1,len(d))*sum(d[x] for x in d)
    
def Thermosensitivity(area):
    Data_2019_df=Conso_2019_df.copy()
    Data_2019_df['Temperature']=Temp_2019_df['Temperature']
    Data_2019_df=Data_2019_df.rename(columns={'Consommation':'Consumption'})
    _,Th_w_2019,Th_s_2019=Decomposeconso2(Data_2019_df,T0=15,T1=20,TemperatureName='Temperature',
                    ConsumptionName='Consumption',TimeName='Date')
    
    Data_df=Variables['total_consumption_Pvar']
    Data_df=Data_df[Data_df.AREAS==area][['TIME','total_consumption_Pvar']].rename(columns={'TIME':'Date','total_consumption_Pvar':'Consumption'}).set_index('Date')
    Data_df['Temperature']=Temp_2019_df['Temperature']+(year-2019)*0.01
    _,Th_w,Th_s=Decomposeconso2(Data_df,T0=15,T1=20,TemperatureName='Temperature',
                    ConsumptionName='Consumption',TimeName='Date')
    
    
    print('Thermosensitivity winter 2019 ={} GW/°C'.format(moyenne_dict(Th_w_2019)))
    print('Thermosensitivity winter '+str(year)+' ={} GW/°C'.format(moyenne_dict(Th_w)))
    print('Thermosensitivity summer 2019 ={} GW/°C'.format(moyenne_dict(Th_s_2019)))
    print('Thermosensitivity summer '+str(year)+' ={} GW/°C'.format(moyenne_dict(Th_s)))
    
    x=list(range(0,24))
    y_w_2019=[-Th_w_2019[x] for x in Th_w_2019]
    y_w=[-Th_w[x] for x in Th_w]
    
    fig_w=go.Figure()
    fig_w.add_trace(go.Scatter(x=x,y=y_w_2019,mode="lines",
        line=go.scatter.Line(color="gray"),name="2019"))
    fig_w.add_trace(go.Scatter(x=x,y=y_w,mode="lines",
        line=go.scatter.Line(color="blue"),name=str(year)))
    fig_w.update_layout(title='En hiver',width = 1000, height = 500)
    fig_w.update_yaxes(title_text = 'Thermosensibilité (GW/°C)')
    fig_w.update_xaxes(title_text = 'Horaire')
    
    y_s_2019=[Th_s_2019[x] for x in Th_s_2019]
    y_s=[Th_s[x] for x in Th_s]
    
    fig_s=go.Figure()
    fig_s.add_trace(go.Scatter(x=x,y=y_s_2019,mode="lines",
        line=go.scatter.Line(color="gray"),name="2019"))
    fig_s.add_trace(go.Scatter(x=x,y=y_s,mode="lines",
        line=go.scatter.Line(color="blue"),name=str(year)))
    fig_s.update_layout(title='En été',width = 1000, height = 500)
    fig_s.update_yaxes(title_text = 'Thermosensibilité (GW/°C)')
    fig_s.update_xaxes(title_text = 'Horaire')
    
    return fig_w, fig_s

def Thermosensitivity_save(area):
    fig_w, fig_s=Thermosensitivity(area)
    fig_w.write_image(InputFolder+"Graphs/Thermo_winter_"+area+"_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus\
                         +".png")
    fig_s.write_image(InputFolder+"Graphs/Thermo_summer_"+area+"_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus\
                         +".png")
        
    
    


In [31]:
fig_w, fig_s=Thermosensitivity('FR')
fig_w.show()
fig_s.show()
#Thermosensitivity_save('FR')

Thermosensitivity winter 2019 =-2545.375218637865 GW/°C
Thermosensitivity winter 2050 =-2138.9978771866367 GW/°C
Thermosensitivity summer 2019 =900.4022823873376 GW/°C
Thermosensitivity summer 2050 =1972.2821092492409 GW/°C


Thermosensitivity winter 2019 =-2545.375218637865 GW/°C
Thermosensitivity winter 2050 =-2138.9978771866367 GW/°C
Thermosensitivity summer 2019 =900.4022823873376 GW/°C
Thermosensitivity summer 2050 =1972.2821092492409 GW/°C


## 2.5. Peak Load

In [32]:
def peak_load(area):
    Conso_df=Variables['total_consumption_Pvar']
    Conso_df=Conso_df[Conso_df.AREAS==area].set_index('TIME')
    H2_df=Variables['storageIn_Pvar']
    H2_df=H2_df[(H2_df.AREAS==area)&(H2_df.STOCK_TECHNO=='PowertoH2toPower')].set_index('TIME')
    Conso_df['total_consumption_Pvar']+=H2_df['storageIn_Pvar']
    return Conso_df[Conso_df['total_consumption_Pvar']==Conso_df['total_consumption_Pvar'].max()]

In [33]:
peak_load('FR')

AREAS  total_consumption_Pvar
TIME                                             
2019-01-28 13:00:00    FR           166442.795359

## 2.6. Consumption

In [34]:
def Conso_years(area='FR',reindus=reindus,bati_hyp=bati_hyp):
    if area=='FR':
        df_ret=pd.DataFrame()
        for year in [2030,2040,2050,2060]:
            with open(InputFolder+"Results_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
            Conso_detailed_year=pd.read_csv("Models/Belfort/Conso/Loads/Conso_detailed_"+str(year)+"_"+reindus+"_"+bati_hyp+".csv",
                                        sep=';',decimal='.',parse_dates=['Date']).set_index(["Date"])
            Conso_sum_year=Conso_detailed_year.sum()
            #print(Conso_sum_year)
            dict_csy={}
            for x in Conso_sum_year.index:
                dict_csy[x]=[Conso_sum_year[x]]
            Conso_sum_year=pd.DataFrame(dict_csy)
            Conso_sum_year['Climatisation et ventilation']+=Conso_sum_year['Conso_TS_air_con']
            
            Conso_sum_year.drop('Conso_TS_air_con',axis=1,inplace=True)
            Conso_sum_year.drop('Taux_pertes',axis=1,inplace=True)
            
            #Conso_flex=Variables_year['flex_consumption_Pvar']
            #Conso_flex=Conso_flex[Conso_flex.AREAS==area]
            #Conso_flex=Conso_flex.groupby(['AREAS','FLEX_CONSUM']).sum()
            #Conso_sum_year['Véhicules électriques']=Conso_flex.loc[(area,'EV'),'flex_consumption_Pvar']
            
            Conso_H2=Variables_year['storageIn_Pvar']
            Conso_H2=Conso_H2[Conso_H2.AREAS==area]
            Conso_H2=Conso_H2.groupby(['AREAS','STOCK_TECHNO']).sum()
            
            Power_H2=Variables_year['storageOut_Pvar']
            Power_H2=Power_H2[Power_H2.AREAS==area]
            Power_H2=Power_H2.groupby(['AREAS','STOCK_TECHNO']).sum()
            Conso_sum_year['Conso_H2']=Conso_H2.loc[(area,'PowertoH2toPower'),'storageIn_Pvar']\
                                        -Power_H2.loc[(area,'PowertoH2toPower'),'storageOut_Pvar']
            
            Pow_df=Variables_year['total_consumption_Pvar']
            Pow_df=Pow_df[Pow_df.AREAS==area]
            P=Pow_df['total_consumption_Pvar'].sum()
            #print(P)
            
            for col in Conso_sum_year.columns:
                if col!='Conso_H2':
                    P-=Conso_sum_year[col]
            Conso_sum_year['Pertes']=P
            Conso_sum_year=Conso_sum_year.rename(columns={'Conso_TS_heat':'Chauffage',
                                                          'Conso_ECS':'Eau chaude sanitaire',
                                                          'Conso_H2':'Hydrogène (électrolyse)',
                                                          'Conso_VE':'Véhicules électrique'})
            Conso_sum_year['Année']=year
            df_ret=pd.concat([df_ret,Conso_sum_year])
        return df_ret.set_index(['Année'])
    else:
        print('Not implemented.')

def Save_conso_years(Conso_years_df,reindus=reindus,bati_hyp=bati_hyp):
    Conso_years_df.to_csv(InputFolder+"Conso_agregates/Conso_secteurs_"+reindus+"_"+bati_hyp+".csv",sep=";",decimal=",",encoding="utf-8")


In [35]:
df=Conso_years()
Save_conso_years(df)

## 2.7. Costs

In [16]:
def costs(area,nuclear_plus_minus=True):
    df_ret=pd.DataFrame()
    for year in [2030,2040,2050,2060]:
        df=pd.DataFrame()
        if year==2030 and nuc!='nuclear_plus_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        elif year!=2060 or not nuclear_plus_minus or nuc!='nuclear_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        else:
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_minus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        
        PowerCosts_df=Variables_year['powerCosts_Pvar']
        PowerCosts_df=PowerCosts_df[PowerCosts_df.AREAS==area].rename(columns={'powerCosts_Pvar':str(year)})
        PowerCosts_df['COST_TYPE']='Energy'
        PowerCosts_df.set_index(['AREAS','COST_TYPE','TECHNOLOGIES'],inplace=True)
        
        CapacityCosts_df=Variables_year['capacityCosts_Pvar']
        CapacityCosts_df=CapacityCosts_df[CapacityCosts_df.AREAS==area].rename(columns={'capacityCosts_Pvar':str(year)})
        CapacityCosts_df['COST_TYPE']='Capacity'
        CapacityCosts_df.set_index(['AREAS','COST_TYPE','TECHNOLOGIES'],inplace=True)
        
        StorageCosts_df=Variables_year['storageCosts_Pvar']
        StorageCosts_df=StorageCosts_df[StorageCosts_df.AREAS==area].rename(columns={'STOCK_TECHNO':'TECHNOLOGIES',
                                                                                    'storageCosts_Pvar':str(year)})
        StorageCosts_df['COST_TYPE']='Storage'
        StorageCosts_df.set_index(['AREAS','COST_TYPE','TECHNOLOGIES'],inplace=True)
        
        FlexCosts_df=Variables_year['flexCosts_Pvar']
        FlexCosts_df=FlexCosts_df[FlexCosts_df.AREAS==area].rename(columns={'FLEX_CONSUM':'TECHNOLOGIES',
                                                                            'flexCosts_Pvar':str(year)})
        FlexCosts_df['COST_TYPE']='Flex'
        FlexCosts_df.set_index(['AREAS','COST_TYPE','TECHNOLOGIES'],inplace=True)
        
        df=pd.concat([PowerCosts_df,CapacityCosts_df,StorageCosts_df,FlexCosts_df])
        C_tot=df[str(year)].sum()
        df_E=Variables_year['power_Dvar']
        df_E=df_E[df_E.AREAS==area]
        E_tot=df_E['power_Dvar'].sum()
        
        #print("Cost {} = {} Mds € and {} €/MWh".format(str(year),C_tot/1e9,C_tot/E_tot))
        df_ret[str(year)]=df[str(year)]
        
    return df_ret

def save_costs(df,area='FR'):
    df.to_csv(InputFolder+"Costs/Costs_"+area+"_"+nuc+"_"+reindus+"_"+bati_hyp+".csv",sep=";",decimal=",",encoding="utf-8")



In [37]:
df=costs('FR')
save_costs(df)

In [38]:
def capa_years(area,nuclear_plus_minus=True):
    df_ret=pd.DataFrame()
    for year in [2030,2040,2050,2060]:
        df=pd.DataFrame()
        if year==2030 and nuc!='nuclear_plus_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        elif year!=2060 or not nuclear_plus_minus or nuc!='nuclear_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        else:
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_minus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        
        Capa_df=Variables_year['capacity_Dvar']
        Capa_df=Capa_df[Capa_df.AREAS==area].rename(columns={'capacity_Dvar':str(year)})
        Capa_df['CAPA_TYPE']='Production'
        Capa_df.set_index(['AREAS','CAPA_TYPE','TECHNOLOGIES'],inplace=True)
        
        StorageIn_df=Variables_year['Pmax_in_Dvar']
        StorageIn_df=StorageIn_df[StorageIn_df.AREAS==area].rename(columns={'STOCK_TECHNO':'TECHNOLOGIES',
                                                                                    'Pmax_in_Dvar':str(year)})
        StorageIn_df['CAPA_TYPE']='Storage_in'
        StorageIn_df.set_index(['AREAS','CAPA_TYPE','TECHNOLOGIES'],inplace=True)
        
        StorageOut_df=Variables_year['Pmax_out_Dvar']
        StorageOut_df=StorageOut_df[StorageOut_df.AREAS==area].rename(columns={'STOCK_TECHNO':'TECHNOLOGIES',
                                                                                    'Pmax_out_Dvar':str(year)})
        StorageOut_df['CAPA_TYPE']='Storage_out'
        StorageOut_df.set_index(['AREAS','CAPA_TYPE','TECHNOLOGIES'],inplace=True)
        
        StorageEn_df=Variables_year['Cmax_Pvar']
        StorageEn_df=StorageEn_df[StorageEn_df.AREAS==area].rename(columns={'STOCK_TECHNO':'TECHNOLOGIES',
                                                                                    'Cmax_Pvar':str(year)})
        StorageEn_df['CAPA_TYPE']='Storage_energy'
        StorageEn_df.set_index(['AREAS','CAPA_TYPE','TECHNOLOGIES'],inplace=True)
        
        Flex_df=Variables_year['increased_max_power_Dvar']
        Flex_df=Flex_df[Flex_df.AREAS==area].rename(columns={'FLEX_CONSUM':'TECHNOLOGIES',
                                                                            'increased_max_power_Dvar':str(year)})
        Flex_df['CAPA_TYPE']='Flex'
        Flex_df.set_index(['AREAS','CAPA_TYPE','TECHNOLOGIES'],inplace=True)
        
        df=pd.concat([Capa_df,StorageIn_df,StorageOut_df,StorageEn_df,Flex_df])
        
        df_ret[str(year)]=df[str(year)]
    return df_ret

def save_capa(df,area='FR'):
    df.to_csv(InputFolder+"Costs/Capacities_"+area+"_"+nuc+"_"+reindus+"_"+bati_hyp+".csv",sep=";",decimal=",",encoding="utf-8")

        

In [39]:
df=capa_years('FR')
save_capa(df)

In [40]:
def imports_exports(area='FR',nuclear_plus_minus=True):
    df_ret=pd.DataFrame()
    for year in [2030,2040,2050,2060]:
        df=pd.DataFrame()
        if year==2030 and nuc!='nuclear_plus_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        elif year!=2060 or not nuclear_plus_minus or nuc!='nuclear_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        else:
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_minus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        
        df_exchange=Variables_year['exchange_Pvar'].copy(deep=True)
        df_exchange.columns=['AREAS_from','AREAS','TIME','exchange_Pvar']
        df_exchange=df_exchange[df_exchange.AREAS==area]
        df_exchange['Imports']=df_exchange['exchange_Pvar'].apply(lambda x: x if x>=0 else 0)
        df_exchange['Exports']=df_exchange['exchange_Pvar'].apply(lambda x: -x if x<0 else 0)
        
        df=df_exchange.groupby(['AREAS_from'])[['Imports','Exports']].sum().reset_index()
        df=pd.melt(df,id_vars=['AREAS_from'],value_vars=['Imports','Exports'],var_name='EXCHANGE_TYPE', value_name=str(year)).set_index(['EXCHANGE_TYPE','AREAS_from'])
        
        df_ret[str(year)]=df[str(year)]
    
    return df_ret

def save_imports_exports(df,area='FR'):
    df.to_csv(InputFolder+"Costs/Imports_Exports_"+area+"_"+nuc+"_"+reindus+"_"+bati_hyp+".csv",sep=";",decimal=",",encoding="utf-8")


In [41]:
df=imports_exports()
save_imports_exports(df)

In [42]:
def costs_countries(nuclear_plus_minus=True,L_areas=['FR','BE','CH','DE','ES','GB','IT']):
    df=pd.DataFrame()
    for area in L_areas:
        df_area=costs(area,nuclear_plus_minus)
        df=pd.concat([df,df_area])
    return df.groupby('AREAS').sum()

def save_costs_countries(df):
    df.to_csv(InputFolder+"Costs/Costs_Europe_"+nuc+"_"+reindus+"_"+bati_hyp+".csv",sep=";",decimal=",",encoding="utf-8")


In [43]:
df=costs_countries()
save_costs_countries(df)

In [44]:
def energy_countries(nuclear_plus_minus=True):
    df_ret=pd.DataFrame()
    for year in [2030,2040,2050,2060]:
        if year==2030 and nuc!='nuclear_plus_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        elif year!=2060 or not nuclear_plus_minus or nuc!='nuclear_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        else:
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_minus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        
        df=Variables_year['power_Dvar']
        df=df.groupby('AREAS').sum()
        df_ret[str(year)]=df['power_Dvar']
    
    return df_ret

def save_energy_countries(df):
    df.to_csv(InputFolder+"Costs/Production_Europe_"+nuc+"_"+reindus+"_"+bati_hyp+".csv",sep=";",decimal=",",encoding="utf-8")
        

In [45]:
df=energy_countries()
save_energy_countries(df)

## 2.8. Costs hydrogen

In [46]:
def H2_costs(nuclear_plus_minus=True):
    df_ret=pd.DataFrame()
    for year in [2030,2040,2050,2060]:
        if year==2030 and nuc!='nuclear_plus_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        elif year!=2060 or not nuclear_plus_minus or nuc!='nuclear_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        else:
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_minus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        
        Conso_FR_df=pd.read_csv("Models/Belfort/Conso/Loads/Conso_"+str(year)+"_"+reindus+"_"+bati_hyp+".csv",
                                sep=';',decimal='.')
        Conso_E_df=pd.read_csv("Models/Belfort/Conso/Conso_Europe/Conso_Europe_"+str(year)+".csv",
                                sep=';',decimal='.')
        
        H2_FR_df=pd.DataFrame({"AREAS":["FR"],"Conso_H2":[Conso_FR_df["Conso_H2"].sum()]})
        H2_FR_df.set_index("AREAS",inplace=True)
        H2_df=Conso_E_df.groupby("AREAS")[["Conso_H2"]].sum()
        H2_df=pd.concat([H2_df,H2_FR_df])
        
        H2_to_power_df=Variables_year['storageOut_Pvar']
        H2_to_power_df=H2_to_power_df[H2_to_power_df.STOCK_TECHNO=='PowertoH2toPower']
        H2_to_power_df=H2_to_power_df.groupby("AREAS")['storageOut_Pvar'].sum()
        H2_df['H2_to_power']=H2_to_power_df
        
        Elec_df=Variables_year['storageIn_Pvar']
        Elec_df=Elec_df[Elec_df.STOCK_TECHNO=='PowertoH2toPower']
        Elec_df=Elec_df.groupby("AREAS")['storageIn_Pvar'].sum()
        H2_df['Electricity_for_H2']=Elec_df
        
        Conso_tot_df=Variables_year['total_consumption_Pvar']
        Conso_tot_df=Conso_tot_df.groupby("AREAS")['total_consumption_Pvar'].sum()
        H2_df['Conso_elec_tot']=Conso_tot_df
        
        Electrolysers_df=Variables_year['Pmax_in_Dvar']
        Electrolysers_df=Electrolysers_df[Electrolysers_df.STOCK_TECHNO=='PowertoH2toPower']
        Electrolysers_df=Electrolysers_df.groupby("AREAS")['Pmax_in_Dvar'].sum()
        H2_df['Electrolysis_capacity']=Electrolysers_df
        
        Storage_df=Variables_year['Cmax_Pvar']
        Storage_df=Storage_df[Storage_df.STOCK_TECHNO=='PowertoH2toPower']
        Storage_df=Storage_df.groupby("AREAS")['Cmax_Pvar'].sum()
        H2_df['Storage_capacity']=Storage_df
        
        H2_df['Year']=year
        H2_df=H2_df.reset_index().set_index(['Year','AREAS'])
        
        df_ret=pd.concat([df_ret,H2_df])
    return df_ret
        
def save_H2_costs(df):
    df.to_csv(InputFolder+"Costs/Costs_H2_"+nuc+"_"+reindus+"_"+bati_hyp+".csv",sep=";",decimal=",",encoding="utf-8")
    

In [47]:
df=H2_costs()
save_H2_costs(df)

In [48]:
H2_costs()

Conso_H2   H2_to_power  Electricity_for_H2  Conso_elec_tot  \
Year AREAS                                                                   
2030 BE     1.969365e+06  0.000000e+00        3.030482e+06    9.210596e+07   
     CH     2.450678e+06  0.000000e+00        3.770273e+06    6.738642e+07   
     DE     2.802048e+07  4.536311e+05        4.457595e+07    5.455885e+08   
     ES     1.157000e+07  0.000000e+00        1.786105e+07    2.715201e+08   
     GB     1.880632e+07  0.000000e+00        2.893555e+07    3.273097e+08   
     IT     1.157794e+07  0.000000e+00        1.782154e+07    3.492305e+08   
     FR     2.582396e+07  0.000000e+00        3.974004e+07    5.190773e+08   
2040 BE     1.045884e+07  0.000000e+00        1.499151e+07    1.035186e+08   
     CH     3.781890e+06  0.000000e+00        5.403988e+06    7.470060e+07   
     DE     7.293349e+07  5.062482e+05        1.057876e+08    6.178295e+08   
     ES     7.233000e+07  0.000000e+00        1.037463e+08    3.083395e+08   
     GB     2.870253e+07  0.000000e+00        4.107299e+07    3.829358e+08   
     IT     3.281256e+07  0.000000e+00        4.711609e+07    3.978090e+08   
     FR     4.365202e+07  0.000000e+00        6.254128e+07    5.950300e+08   
2050 BE     2.434433e+07  3.839105e+05        3.582779e+07    1.185747e+08   
     CH     5.641544e+06  0.000000e+00        8.065823e+06    8.279532e+07   
     DE     1.405590e+08  2.075669e+07        2.533916e+08    7.027562e+08   
     ES     1.221200e+08  0.000000e+00        1.749583e+08    3.466006e+08   
     GB     4.256843e+07  1.532230e+06        6.475013e+07    4.355693e+08   
     IT     6.182463e+07  1.501341e+06        9.256113e+07    4.501823e+08   
     FR     6.725214e+07  0.000000e+00        9.621154e+07    6.827569e+08   
2060 BE     2.434433e+07  4.848870e+05        3.612521e+07    1.192315e+08   
     CH     6.061679e+06  0.000000e+00        8.666310e+06    8.361300e+07   
     DE     1.405590e+08  2.023548e+07        2.520855e+08    7.038021e+08   
     ES     1.221200e+08  0.000000e+00        1.750074e+08    3.449217e+08   
     GB     4.544443e+07  2.296736e+06        7.076103e+07    4.427378e+08   
     IT     6.182463e+07  1.374026e+06        9.221529e+07    4.471054e+08   
     FR     6.956806e+07  0.000000e+00        9.952057e+07    6.865314e+08   

            Electrolysis_capacity  Storage_capacity  
Year AREAS                                           
2030 BE                348.808985      1.070118e+04  
     CH                430.396488      0.000000e+00  
     DE               5427.343340      8.620631e+05  
     ES               4612.761967      8.117389e+05  
     GB               3312.672359      4.018154e+04  
     IT               2063.085487      9.984557e+04  
     FR               4617.089297      1.995629e+05  
2040 BE               3466.012516      5.927617e+05  
     CH                632.325213      3.478142e+04  
     DE              29280.282707      4.604083e+06  
     ES              24596.522345      5.142672e+06  
     GB               8371.389894      1.024154e+06  
     IT              10798.669032      3.164117e+06  
     FR              14313.508171      2.042312e+06  
2050 BE               9181.311203      1.257568e+06  
     CH               1011.358368      1.250285e+05  
     DE              62741.438390      1.767526e+07  
     ES              43629.290466      6.518151e+06  
     GB              15895.101157      2.278224e+06  
     IT              20714.084703      6.134723e+06  
     FR              17755.324507      1.742103e+06  
2060 BE              10509.429030      1.626204e+06  
     CH               1114.918953      1.325464e+05  
     DE              63211.872037      1.682146e+07  
     ES              44559.176107      6.828017e+06  
     GB              16505.936328      2.558518e+06  
     IT              21098.859916      6.427697e+06  
     FR              18786.893578      1.861302e+06

In [34]:
def elec_for_H2_costs(nuclear_plus_minus=True):
    df_ret=pd.DataFrame()
    for year in [2030,2040,2050,2060]:
        if year==2030 and nuc!='nuclear_plus_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        elif year!=2060 or not nuclear_plus_minus or nuc!='nuclear_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        else:
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_minus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        
        Capa_costs=Variables_year['capacityCosts_Pvar'].groupby("AREAS")['capacityCosts_Pvar'].sum()
        Power_costs=Variables_year['powerCosts_Pvar'].groupby("AREAS")['powerCosts_Pvar'].sum()
        Sto_costs=Variables_year['storageCosts_Pvar']
        Sto_costs=Sto_costs[Sto_costs.STOCK_TECHNO!='PowertoH2toPower'].groupby("AREAS")['storageCosts_Pvar'].sum()
        Flex_costs=Variables_year['flexCosts_Pvar'].groupby("AREAS")['flexCosts_Pvar'].sum()
        df_ret[str(year)]=Capa_costs+Power_costs+Sto_costs+Flex_costs
        
    return df_ret

def save_elec_for_H2_costs(df):
    df.to_csv(InputFolder+"Costs/Costs_elec_for_H2_"+nuc+"_"+reindus+"_"+bati_hyp+".csv",sep=";",decimal=",",encoding="utf-8")
    

In [35]:
df=elec_for_H2_costs()
save_elec_for_H2_costs(df)
df

2030          2040          2050          2060
AREAS                                                        
BE     7.155358e+09  7.145314e+09  8.092929e+09  8.491272e+09
CH     3.050679e+09  3.449127e+09  3.942573e+09  4.003152e+09
DE     4.675558e+10  4.662840e+10  4.809583e+10  4.841964e+10
ES     1.603360e+10  2.112915e+10  2.204552e+10  2.217469e+10
FR     3.169660e+10  3.721764e+10  3.802127e+10  3.867107e+10
GB     3.174666e+10  2.993888e+10  3.081923e+10  3.058528e+10
IT     2.399276e+10  2.597372e+10  2.802368e+10  2.800407e+10

In [36]:
def capa_enr_europe(nuclear_plus_minus=True):
    df_ret=pd.DataFrame()
    for year in [2030,2040,2050,2060]:
        if year==2030 and nuc!='nuclear_plus_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        elif year!=2060 or not nuclear_plus_minus or nuc!='nuclear_plus':
            with open(InputFolder+"Results_"+type_result+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        else:
            with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_minus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
        
        df=Variables_year['capacity_Dvar']
        df=df[(df.TECHNOLOGIES=='WindOffShore')|(df.TECHNOLOGIES=='WindOnShore')|(df.TECHNOLOGIES=='Solar')].set_index(['AREAS','TECHNOLOGIES'])
        
        df_ret[str(year)]=df['capacity_Dvar']
    return df_ret
        
def save_capa_enr_europe(df):
    df.to_csv(InputFolder+"Costs/Capa_enr_europe_"+nuc+"_"+reindus+"_"+bati_hyp+".csv",sep=";",decimal=",",encoding="utf-8")
 

In [37]:
df=capa_enr_europe()
save_capa_enr_europe(df)
df

2030           2040           2050           2060
AREAS TECHNOLOGIES                                                           
BE    Solar         13788.000000   23788.000000   33788.000000   33788.000000
      WindOnShore    4429.000000   17762.417513   18908.694726   20822.901710
      WindOffShore   9016.000000   15778.000000   28478.630255   30513.018240
CH    Solar         14500.000000   27200.000000   39179.021985   40000.000000
      WindOnShore     700.000000    1400.000000    2100.000000    2100.000000
      WindOffShore      0.000000       0.000000       0.000000       0.000000
FR    Solar         48069.553346  128030.491295  160215.865202  170126.052839
      WindOnShore   23400.000000   30200.000000   37000.000000   37000.000000
      WindOffShore  15200.000000   32100.000000   49000.000000   49000.000000
ES    Solar         67528.790753  129580.234015  146350.609867  148225.555857
      WindOnShore   41235.000000   56235.000000   71235.000000   71235.000000
      WindOffShore  10000.000000   25000.000000   40000.000000   40000.000000
GB    Solar         22378.000000   66436.322657   42400.000000   42400.000000
      WindOnShore   21937.000000   31937.000000   41937.000000   41937.000000
      WindOffShore  35000.000000   69342.855926   85800.000000   85800.000000
DE    Solar         98538.000000  151156.581394  252837.732718  257466.594944
      WindOnShore   78000.000000  104000.000000  130000.000000  130000.000000
      WindOffShore  46644.000000   81627.000000  116610.000000  116610.000000
IT    Solar         63800.000000  148195.105395  179444.440638  179249.824740
      WindOnShore   46400.000000   85700.000000  125000.000000  125000.000000
      WindOffShore   1000.000000    1000.000000    1000.000000    1000.000000

## 2.9. Consumption curves

In [49]:
def filter_variable_2(name,area,month,day,hour_ini):
    df=Variables[name]
    d0=datetime(2019,month,day,hour_ini)
    d1=d0+timedelta(hours=24)
    df1=df['TIME'].apply(lambda x: 1 if x>=d0 and x<d1 else 0)
    return df[(df1==1)&(df.AREAS==area)]

def conso_flex_df(area,conso_type,month,day,hour_ini):
    df=Variables['flex_consumption_Pvar']
    df=filter_variable_2('flex_consumption_Pvar',area,month,day,hour_ini)
    df=df[df.FLEX_CONSUM==conso_type]
    return df[['TIME','flex_consumption_Pvar']].set_index('TIME').sort_index()

def conso_flex_mean_df(area,conso_type):
    df=Variables['flex_consumption_Pvar'].copy()
    df=df[(df.FLEX_CONSUM==conso_type)&(df.AREAS==area)]
    df['hour']=df['TIME'].apply(lambda x: x.hour)
    df1=df.groupby('hour').mean()
    return df1[['flex_consumption_Pvar']]
    

In [50]:
conso_flex_mean_df('FR','EV')

flex_consumption_Pvar
hour                       
0               3552.428464
1               4861.463721
2               4091.843122
3               3865.858329
4               3712.038279
5               3350.297447
6               1435.806932
7               1643.545838
8               2406.579803
9               9968.066781
10             18816.344266
11             24514.370734
12             30185.156361
13             36881.430849
14             34864.085723
15             28317.493206
16             25220.207143
17             15415.201093
18             18628.325127
19              2470.563837
20               641.460899
21              1189.972900
22              4178.666486
23              3656.874021

In [51]:
conso_flex_mean_df('FR','Steel')

flex_consumption_Pvar
hour                       
0               1395.204467
1               1424.083071
2               1334.168548
3               1390.510883
4               1296.678002
5               1190.339148
6               6541.398372
7               6546.392854
8               7022.759285
9               7964.199208
10              8665.338003
11              8966.537297
12              8950.405646
13              8895.811298
14              8929.039986
15              8851.779204
16              8595.883292
17              8168.622682
18              6966.167445
19              7031.263438
20              6793.834204
21              6755.422569
22              1274.022421
23              1367.065429

In [52]:
def conso_natural_mean_df(area,conso_type):
    if area=='FR':
        df=pd.read_csv("Models/Belfort/Conso/Loads/Conso_detailed_"+str(year)+"_"+reindus+"_"+bati_hyp+".csv",
                   sep=";",decimal=".",parse_dates=['Date'])
        df['hour']=df['Date'].dt.hour
        df=df[[conso_type,'hour']].groupby('hour').mean()
        return df
    else:
        print("Not implemented.")

In [53]:
conso_natural_mean_df('FR','Metallurgie')

Metallurgie
hour             
0     6084.983497
1     5707.314727
2     5738.844691
3     5725.134555
4     5615.955479
5     5470.669178
6     5287.093375
7     5282.075950
8     5412.508421
9     5592.153050
10    5700.022676
11    5649.105404
12    5697.094720
13    5977.110568
14    5903.890657
15    5925.181789
16    5880.644933
17    5608.851459
18    5283.915337
19    5512.102082
20    5916.908223
21    5914.801347
22    5445.679783
23    5984.884852

## 2.10. Storage curves (H2)

In [54]:
def storage_curve(area,year=year,stock_techno='PowertoH2toPower'):
    d_colors={'nuclear_plus_plus':'goldenrod','nuclear_plus':'gold','nuclear_minus':'yellow','100_enr':'gray'}
    d_nuc={'nuclear_plus_plus':'Nucléaire ++','nuclear_plus':'Nucléaire +','nuclear_minus':'Nucléaire -','100_enr':'Sans EPR'}
    fig=go.Figure()
    if year==2030:
        with open(InputFolder+"Results_"+type_result+str(year)+"_nuclear_plus_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
            Variables_year=pickle.load(f)
        df=Variables_year['stockLevel_Pvar'].copy()
        df=df[(df.AREAS==area)&(df.STOCK_TECHNO==stock_techno)]
        df=df.set_index('TIME').sort_index().reset_index()
        df['TIME']=df['TIME'].apply(lambda x: x.replace(year=year))
        fig.add_trace(go.Scatter(x= df['TIME'], y = df['stockLevel_Pvar']/1e6,
                                     mode="lines",
                                     line=go.scatter.Line(color="gold"),name='Nucléaire +'))
    else:    
        for nuc in ['nuclear_plus_plus','nuclear_plus','nuclear_minus','100_enr']:
            if year==2060 and nuc=='nuclear_plus':
                nuc1='nuclear_plus_minus'
            else:
                nuc1=nuc
            
            with open(InputFolder+"Results_"+type_result+str(year)+"_"+nuc1+"_"+bati_hyp+"_"+reindus+".pickle", 'rb') as f:
                Variables_year=pickle.load(f)
            df=Variables_year['stockLevel_Pvar'].copy()
            df=df[(df.AREAS==area)&(df.STOCK_TECHNO==stock_techno)]
            df=df.set_index('TIME').sort_index().reset_index()
            df['TIME']=df['TIME'].apply(lambda x: x.replace(year=year))
            fig.add_trace(go.Scatter(x= df['TIME'], y = df['stockLevel_Pvar']/1e6,
                                     mode="lines",
                                     line=go.scatter.Line(color=d_colors[nuc]),name=d_nuc[nuc]))
        
    fig.update_layout(width = 1000, height = 500)
    fig.update_yaxes(title_text = 'Énergie stockée (TWh PCI)')
    return fig

def plot_and_save_storage_curve(area,year=year,stock_techno='PowertoH2toPower'):
    fig=storage_curve(area,year,stock_techno)
    fig.write_image(InputFolder+"Graphs/Storage_"+stock_techno+"_"+type_result+area+"_"+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus+".png")
    fig.show()
    

In [55]:
plot_and_save_storage_curve('FR',2060)

## 2.11. Monotones de puissance

In [56]:
def filter_energy(df,energy):
    if energy=='ENRI':
        df=df[(df.TECHNOLOGIES=='Solar')|(df.TECHNOLOGIES=='WindOnShore')|
              (df.TECHNOLOGIES=='WindOffShore')]
    elif energy=='Wind':
        df=df[(df.TECHNOLOGIES=='WindOnShore')|(df.TECHNOLOGIES=='WindOffShore')]
    else:
        df=df[df.TECHNOLOGIES==energy]
    return df

def monotone(area,energy):
    df=Variables['power_Dvar'].copy()
    df_cap=Variables['capacity_Dvar'].copy()
    df=filter_energy(df,energy)
    df_cap=filter_energy(df_cap,energy)
    if area!='EU':
        df=df[df.AREAS==area]
        df_cap=df_cap[df_cap.AREAS==area]
    df=df.groupby('TIME').sum()
    P=df_cap['capacity_Dvar'].sum()
    df=df.sort_values(by='power_Dvar',ascending=False)
    df['power_Dvar']=df['power_Dvar']/P
    return df

d_areas={'FR':'France','BE':'Belgique','CH':'Suisse','DE':'Allemagne',
         'ES':'Espagne','GB':'Grande-Bretagne','IT':'Italie'}
d_colors={'Solar':('orange','orangered'),'WindOnShore':('cornflowerblue','navy'),
          'WindOffShore':('cornflowerblue','navy'),'Wind':('cornflowerblue','navy'),
          'ENRI':('limegreen','forestgreen')}
def plot_monotone(energy,title='',area='FR'):
    df_eu=monotone('EU',energy)
    df_area=monotone(area,energy)
    x=np.linspace(0,8760,8760)
    fig=go.Figure()
    fig.add_trace(go.Scatter(x=x, y=df_area['power_Dvar'],
                                     mode="lines",
                                     line=go.scatter.Line(color=d_colors[energy][0]),name=d_areas[area]))
    fig.add_trace(go.Scatter(x=x, y=df_eu['power_Dvar'],
                                     mode="lines",
                                     line=go.scatter.Line(color=d_colors[energy][1]),name="Europe de l'Ouest"))
    fig.update_layout(title=title,title_x=0.5,width = 700, height = 500)
    fig.update_yaxes(title_text = 'Facteur de charge')
    fig.update_xaxes(title_text = 'Temps (heures)')
    
    return fig

def save_monotone(fig,energy):
    fig.write_image(InputFolder+"Graphs/Monotone_"+energy+"_"+str(year)+"_"+nuc+"_"+bati_hyp+"_"+reindus+".png")

In [57]:
fig_solar=plot_monotone('Solar','Monotone de puissance solaire')
fig_wind=plot_monotone('Wind','Monotone de puissance éolienne')
fig_enri=plot_monotone('ENRI','Monotone de puissance éolienne et solaire')
fig_solar.show()
fig_wind.show()
fig_enri.show()
save_monotone(fig_solar,'Solar')
save_monotone(fig_wind,'Wind')
save_monotone(fig_enri,'ENRI')